#Automático de Balances de Energía por Kathiana Murillo
##Problema
El proceso manual del cálculo del balance realizado por el analista de mercados enfrenta varios problemas: Horarios de la entrega de los datos (retrasos en la entrega) , Calidad y precisión de los datos para el balance, Falta de estandarización de la información (genera errores en la fuente de datos), Consolidado de la información, imprecisiones en los cálculos realizados, cumplimiento de los plazos establecidos para la entrega del informe final.

En este proceso la ETL se encargará de extraer la información de las fuentes de forma remota, para luego transformar a un formato manejable, la cruzará y filtrará, y finalmente la disponibilizará para descarga en un destino para que los analistas o el regulador la usen.

##Fuentes
- Descarga Archivo de despacho horario de las centrales de energia consolidado.
- Consumo de API de despacho programado para la fecha del ente regulador.
- Consumo de API de Precio de la energia por kWh para el día asignado.



### Preparación de prerequisitos

En esta sección se instalan los paquetes, librerías y componentes que le permitirán al pipeline realizar sus procesos internos.

In [0]:
%sh
pip install openpyxl xlrd pydrive

  Obtaining dependency information for openpyxl from https://files.pythonhosted.org/packages/c0/da/977ded879c29cbd04de313843e76868e6e13408a94ed6b987245dc7c8506/openpyxl-3.1.5-py2.py3-none-any.whl.metadata
  Obtaining dependency information for xlrd from https://files.pythonhosted.org/packages/a6/0c/c2a72d51fe56e08a08acc85d13013558a2d793028ae7385448a6ccdfae64/xlrd-2.0.1-py2.py3-none-any.whl.metadata
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 987.4/987.4 kB 8.9 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Obtaining dependency information for et-xmlfile from https://files.pythonhosted.org/packages/96/c2/3dd434b0108730014f1b96fd286040dc3bcb70066346f7e01ec2ac95865f/et_xmlfile-1.1.0-py3-none-any.whl.metadata
  Obtaining dependency information for google-api-python-client>=1.2 from https://files.pythonhosted.org/packages/e6/53/4e109982df222687dea9e736499c69076d7d00699a14470ee281c5cf9eed/google_api_python_client-2.14


[notice] A new release of pip is available: 23.2.1 -> 24.2
[notice] To update, run: pip install --upgrade pip


## Declaracion de Librerías y Variables

En estas dos celdas importamos las librerías de Python y frameworks como Pandas y definimos las variables:

- Fecha de inicio del balance.
- Fecha final del balance.
- Identificación del archivo publico de despacho de generacion.


In [0]:
import requests
import pandas as pd


In [0]:
# Variables
fecha_inicio = "2024-06-09"
fecha_fin = "2024-06-20"
id_archivo_balance_drive = "1kXBIgeXQzM6i1slWQE0vuiPsdgFCSUy2"
api_key_1 = "BzctZym8mKm8vnn10ASmWOaYXsWIm6hJdkripJAUXe9rXdt6FbS6NDVZMf8Fsph0"
api_key_2 = "jsTEumwIybpuXobpqQJyFCFJtYhxkvPKMVHVnVl9elFRGvxzjLiSINouZVPBTKwV"

# (E) Fuentes

### (*E*) Extraccion del API de Precios de la Energía

Aquí descargamos del API los datos en formato JSON, usamos una librería nativa de Python llamada Requests y con ella consumimos el api de la URL, y almacenamos el resultado en una estructura de datos denominada un dataframe, que servirá para procesamiento posterior.

### (*E*) Extraccion del Plan de Despacho de Energía por Unidad y Central

Aqui descargamos del API los datos del despacho en formato JSON, usamos una librería nativa de Python llamada Requests y con ella consumimos el api de la URL, y almacenamos el resultado en una estructura de datos denominada un dataframe, que servirá para procesamiento posterior.

### (*E*) Descarga del archivo con nuestros datos reales de generación

En estas 2 celdas, descargamos de Google Drive nuestro archivo de consolidado de generación, igual que antes, usamos Requests y con ella descargamos el archivo de la URL, en este caso tenemos que traer el archivo a una ubicación local, y posteriormente lo cargamos con Pandas, un framework de procesamiento de datos de python para analítica, y lo cargamos como un dataframe de Pandas.

In [0]:
# Descargar datos de precios de bolsa
url_precios = f"https://www.simem.co/backend-files/api/PublicData?startDate={fecha_inicio}&endDate={fecha_fin}&datasetId=96D56E"
response = requests.get(url_precios)

# Verificar la respuesta
if response.status_code == 200:
    data = response.json()
    if 'result' in data and 'records' in data['result']:
        # Normalizar los datos JSON a un DataFrame
        df_precios = pd.json_normalize(data['result']['records'])
        print("Datos de precios de bolsa descargados y procesados correctamente.")
    else:
        print("La estructura de datos en la respuesta no es la esperada.")
        df_precios = pd.DataFrame()
else:
    print(f"Error al descargar los datos: {response.status_code}")
    df_precios = pd.DataFrame()

display(df_precios)

Datos de precios de bolsa descargados y procesados correctamente.


CodigoVariable Fecha CodigoDuracion UnidadMedida Version Valor PPBOGReal 2024-06-20 P1D COP/kWh TXF 322.0811 PPBO 2024-06-20 P1D COP/kWh TXF 316.4945 PPBOGReal 2024-06-20 P1D COP/kWh TX2 308.2125 PPBO 2024-06-20 P1D COP/kWh TX2 302.7103 PPBO 2024-06-20 P1D COP/kWh TX3 316.9398 PPBOGReal 2024-06-20 P1D COP/kWh TX3 322.5297 PPBO 2024-06-20 P1D COP/kWh TXR 316.4859 PPBOGReal 2024-06-20 P1D COP/kWh TXR 322.0841 PPBOGReal 2024-06-20 P1D COP/kWh TX1 308.2145 PPBOGReal 2024-06-19 P1D COP/kWh TX2 304.5383 PPBO 2024-06-19 P1D COP/kWh TX2 296.5202 PPBOGReal 2024-06-19 P1D COP/kWh TX1 304.6868 PPBO 2024-06-19 P1D COP/kWh TXF 310.2923 PPBOGReal 2024-06-19 P1D COP/kWh TXF 318.4077 PPBO 2024-06-19 P1D COP/kWh TX3 311.186 PPBOGReal 2024-06-19 P1D COP/kWh TX3 319.3001 PPBO 2024-06-19 P1D COP/kWh TXR 310.2853 PPBOGReal 2024-06-19 P1D COP/kWh TXR 318.4008 PPBOGReal 2024-06-18 P1D COP/kWh TX3 246.8571 PPBO 2024-06-18 P1D COP/kWh TX3 239.8 PPBOGReal 2024-06-18 P1D COP/kWh TXF 243.9286 PPBO 2024-06-18 P1D COP/kWh TXF 236.8524 PPBO 2024-06-18 P1D COP/kWh TXR 236.855 PPBOGReal 2024-06-18 P1D COP/kWh TXR 243.9302 PPBO 2024-06-18 P1D COP/kWh TX2 223.2199 PPBOGReal 2024-06-18 P1D COP/kWh TX2 230.0602 PPBOGReal 2024-06-18 P1D COP/kWh TX1 236.8389 PPBOGReal 2024-06-17 P1D COP/kWh TX3 262.5281 PPBO 2024-06-17 P1D COP/kWh TX3 261.1931 PPBOGReal 2024-06-17 P1D COP/kWh TX2 248.4987 PPBO 2024-06-17 P1D COP/kWh TX2 247.0964 PPBOGReal 2024-06-17 P1D COP/kWh TX1 248.4904 PPBO 2024-06-17 P1D COP/kWh TXF 261.0419 PPBOGReal 2024-06-17 P1D COP/kWh TXF 262.3524 PPBO 2024-06-17 P1D COP/kWh TXR 261.0373 PPBOGReal 2024-06-17 P1D COP/kWh TXR 262.3544 PPBOGReal 2024-06-16 P1D COP/kWh TXF 278.2515 PPBO 2024-06-16 P1D COP/kWh TXF 276.6197 PPBOGReal 2024-06-16 P1D COP/kWh TX1 264.3685 PPBOGReal 2024-06-16 P1D COP/kWh TX2 264.3774 PPBO 2024-06-16 P1D COP/kWh TX2 262.811 PPBOGReal 2024-06-16 P1D COP/kWh TX3 278.2651 PPBO 2024-06-16 P1D COP/kWh TX3 276.6307 PPBO 2024-06-16 P1D COP/kWh TXR 276.6194 PPBOGReal 2024-06-16 P1D COP/kWh TXR 278.2526 PPBOGReal 2024-06-15 P1D COP/kWh TXF 294.9338 PPBO 2024-06-15 P1D COP/kWh TXF 290.0569 PPBO 2024-06-15 P1D COP/kWh TX2 274.5118 PPBOGReal 2024-06-15 P1D COP/kWh TX1 275.5262 PPBOGReal 2024-06-15 P1D COP/kWh TX2 279.8025 PPBOGReal 2024-06-15 P1D COP/kWh TX3 294.9832 PPBO 2024-06-15 P1D COP/kWh TX3 290.11 PPBOGReal 2024-06-15 P1D COP/kWh TXR 294.9351 PPBO 2024-06-15 P1D COP/kWh TXR 290.0608 PPBOGReal 2024-06-14 P1D COP/kWh TXR 372.0906 PPBO 2024-06-14 P1D COP/kWh TXR 370.9428 PPBO 2024-06-14 P1D COP/kWh TX3 370.9896 PPBOGReal 2024-06-14 P1D COP/kWh TX3 372.1355 PPBO 2024-06-14 P1D COP/kWh TXF 370.9397 PPBOGReal 2024-06-14 P1D COP/kWh TXF 372.0884 PPBOGReal 2024-06-14 P1D COP/kWh TX2 358.223 PPBO 2024-06-14 P1D COP/kWh TX2 357.0756 PPBOGReal 2024-06-14 P1D COP/kWh TX1 357.8701 PPBO 2024-06-13 P1D COP/kWh TX2 344.8023 PPBOGReal 2024-06-13 P1D COP/kWh TX2 349.1387 PPBOGReal 2024-06-13 P1D COP/kWh TX3 363.0519 PPBO 2024-06-13 P1D COP/kWh TX3 358.8017 PPBOGReal 2024-06-13 P1D COP/kWh TXF 363.0057 PPBO 2024-06-13 P1D COP/kWh TXF 358.7517 PPBO 2024-06-13 P1D COP/kWh TXR 358.758 PPBOGReal 2024-06-13 P1D COP/kWh TXR 363.0072 PPBOGReal 2024-06-13 P1D COP/kWh TX1 348.7421 PPBO 2024-06-12 P1D COP/kWh TXR 334.1408 PPBOGReal 2024-06-12 P1D COP/kWh TXR 337.7336 PPBOGReal 2024-06-12 P1D COP/kWh TXF 337.7326 PPBO 2024-06-12 P1D COP/kWh TXF 334.1386 PPBO 2024-06-12 P1D COP/kWh TX3 334.2483 PPBOGReal 2024-06-12 P1D COP/kWh TX3 337.8306 PPBOGReal 2024-06-12 P1D COP/kWh TX2 323.8557 PPBOGReal 2024-06-12 P1D COP/kWh TX1 323.8685 PPBO 2024-06-12 P1D COP/kWh TX2 319.8822 PPBOGReal 2024-06-11 P1D COP/kWh TXF 309.7453 PPBO 2024-06-11 P1D COP/kWh TXF 305.2788 PPBO 2024-06-11 P1D COP/kWh TX3 305.5111 PPBOGReal 2024-06-11 P1D COP/kWh TX3 309.984 PPBOGReal 2024-06-11 P1D COP/kWh TXR 309.734 PPBO 2024-06-11 P1D COP/kWh TXR 305.2707 PPBOGReal 2024-06-11 P1D COP/kWh TX1 295.6238 PPBO 2024-06-11 P1D COP/kWh TX2 291.1207 PPBOGReal 2024-06-11 P1D COP/kWh TX2 295.8824 PPBO 2024

In [0]:
# Descargar datos de despachos
url_despachos = f"https://www.simem.co/backend-files/api/PublicData?startdate={fecha_inicio}&enddate={fecha_fin}&datasetId=ff027b"
response = requests.get(url_despachos)

# Verificar la respuesta
if response.status_code == 200:
    data = response.json()
    if 'result' in data and 'records' in data['result']:
        # Normalizar los datos JSON a un DataFrame
        df_despachos = pd.json_normalize(data['result']['records'])
        print("Datos de despachos descargados y procesados correctamente.")
    else:
        print("La estructura de datos en la respuesta no es la esperada.")
        df_despachos = pd.DataFrame()
else:
    print(f"Error al descargar los datos: {response.status_code}")
    df_despachos = pd.DataFrame()

display(df_despachos)

Datos de despachos descargados y procesados correctamente.


FechaHora CodigoDuracion CodigoPlanta Valor 2024-06-20 01:00:00 PT1H 3EFY 0.0 2024-06-20 01:00:00 PT1H 3ENA 0.0 2024-06-20 01:00:00 PT1H 3ENE 0.0 2024-06-20 01:00:00 PT1H 3EP6 0.0 2024-06-20 01:00:00 PT1H 3EV1 0.0 2024-06-20 01:00:00 PT1H 3EV3 0.0 2024-06-20 01:00:00 PT1H 3EXB 0.0 2024-06-20 01:00:00 PT1H 3EXH 8150.0 2024-06-20 01:00:00 PT1H 3F5L 0.0 2024-06-20 01:00:00 PT1H 3F5N 0.0 2024-06-20 01:00:00 PT1H 3FCD 0.0 2024-06-20 01:00:00 PT1H 3FCF 0.0 2024-06-20 01:00:00 PT1H 3GI6 0.0 2024-06-20 01:00:00 PT1H 3GJQ 0.0 2024-06-20 01:00:00 PT1H 3GJU 500.0 2024-06-20 01:00:00 PT1H 3GPZ 0.0 2024-06-20 01:00:00 PT1H 3GRD 0.0 2024-06-20 01:00:00 PT1H 3GSF 0.0 2024-06-20 01:00:00 PT1H 3GVI 0.0 2024-06-20 01:00:00 PT1H 3GVK 0.0 2024-06-20 01:00:00 PT1H 3GVM 0.0 2024-06-20 01:00:00 PT1H 3H2U 9800.0 2024-06-20 01:00:00 PT1H 3HBN 0.0 2024-06-20 01:00:00 PT1H 3HBP 0.0 2024-06-20 01:00:00 PT1H 3HDE 19920.0 2024-06-20 01:00:00 PT1H 3HDG 19920.0 2024-06-20 01:00:00 PT1H 3HE8 0.0 2024-06-20 01:00:00 PT1H 3HF5 0.0 2024-06-20 01:00:00 PT1H 3HF7 0.0 2024-06-20 01:00:00 PT1H 3HF9 0.0 2024-06-20 01:00:00 PT1H 3HG7 0.0 2024-06-20 01:00:00 PT1H 3HG9 0.0 2024-06-20 01:00:00 PT1H 3HLD 0.0 2024-06-20 01:00:00 PT1H 3HS9 0.0 2024-06-20 01:00:00 PT1H 3HWM 0.0 2024-06-20 01:00:00 PT1H 3HYG 0.0 2024-06-20 01:00:00 PT1H 3IJF 1000.0 2024-06-20 01:00:00 PT1H 3INX 0.0 2024-06-20 01:00:00 PT1H 3IQA 0.0 2024-06-20 01:00:00 PT1H 3IRX 0.0 2024-06-20 01:00:00 PT1H 3IRZ 700.0 2024-06-20 01:00:00 PT1H 3IS2 0.0 2024-06-20 01:00:00 PT1H 3IZ6 0.0 2024-06-20 01:00:00 PT1H 3J1J 0.0 2024-06-20 01:00:00 PT1H 3J2B 0.0 2024-06-20 01:00:00 PT1H 3J2H 0.0 2024-06-20 01:00:00 PT1H 3J4D 0.0 2024-06-20 01:00:00 PT1H 2TYI 0.0 2024-06-20 01:00:00 PT1H 2U1G 1400.0 2024-06-20 01:00:00 PT1H 2U5P 0.0 2024-06-20 01:00:00 PT1H 2U8Y 19300.0 2024-06-20 01:00:00 PT1H 2U91 19300.0 2024-06-20 01:00:00 PT1H 2U93 19300.0 2024-06-20 01:00:00 PT1H 2UP2 1000.0 2024-06-20 01:00:00 PT1H 2UPD 9000.0 2024-06-20 01:00:00 PT1H 2UPF 9000.0 2024-06-20 01:00:00 PT1H 2UPH 9000.0 2024-06-20 01:00:00 PT1H 2UPJ 9000.0 2024-06-20 01:00:00 PT1H 2UR5 750.0 2024-06-20 01:00:00 PT1H 2UX3 16400.0 2024-06-20 01:00:00 PT1H 2V25 900.0 2024-06-20 01:00:00 PT1H 2V27 400.0 2024-06-20 01:00:00 PT1H 2V5G 2900.0 2024-06-20 01:00:00 PT1H 2VJS 0.0 2024-06-20 01:00:00 PT1H 2WC5 7000.0 2024-06-20 01:00:00 PT1H 2WFN 3000.0 2024-06-20 01:00:00 PT1H 2XXR 0.0 2024-06-20 01:00:00 PT1H 2YB9 1000.0 2024-06-20 01:00:00 PT1H 2YIR 210.0 2024-06-20 01:00:00 PT1H 2YNA 3100.0 2024-06-20 01:00:00 PT1H 2YWY 3500.0 2024-06-20 01:00:00 PT1H 2ZCF 10000.0 2024-06-20 01:00:00 PT1H 2ZHY 0.0 2024-06-20 01:00:00 PT1H 2ZP9 0.0 2024-06-20 01:00:00 PT1H 3A44 0.0 2024-06-20 01:00:00 PT1H 3ACC 0.0 2024-06-20 01:00:00 PT1H 3ADA 380.0 2024-06-20 01:00:00 PT1H 3AFQ 1000.0 2024-06-20 01:00:00 PT1H 3AQP 200.0 2024-06-20 01:00:00 PT1H 3B4L 0.0 2024-06-20 01:00:00 PT1H 3BZB 0.0 2024-06-20 01:00:00 PT1H 3C3X 200.0 2024-06-20 01:00:00 PT1H 3C3Z 0.0 2024-06-20 01:00:00 PT1H 3C4V 2800.0 2024-06-20 01:00:00 PT1H 3CG9 4000.0 2024-06-20 01:00:00 PT1H 3CSH 0.0 2024-06-20 01:00:00 PT1H 3DDT 0.0 2024-06-20 01:00:00 PT1H 3DSO 0.0 2024-06-20 01:00:00 PT1H 3DXJ 450.0 2024-06-20 01:00:00 PT1H 3E7C 0.0 2024-06-20 01:00:00 PT1H 3E9I 8000.0 2024-06-20 01:00:00 PT1H 3EBN 0.0 2024-06-20 01:00:00 PT1H 3ED1 0.0 2024-06-20 01:00:00 PT1H 3EDL 0.0 2024-06-20 01:00:00 PT1H 3EE4 11480.0 2024-06-20 01:00:00 PT1H CCN1 2800.0 2024-06-20 01:00:00 PT1H CGM1 17000.0 2024-06-20 01:00:00 PT1H CHBG 498000.0 2024-06-20 01:00:00 PT1H CHVR 0.0 2024-06-20 01:00:00 PT1H CIP1 12500.0 2024-06-20 01:00:00 PT1H CIS1 0.0 2024-06-20 01:00:00 PT1H CLDR 10000.0 2024-06-20 01:00:00 PT1H CLL1 78000.0 2024-06-20 01:00:00 PT1H CLMG 0.0 2024-06-20 01:00:00 PT1H CMN1 7800.0 2024-06-20 01:00:00 PT1H CMP2 0.0 2024-06-20 01:00:00 PT1H COE1 1100.0 2024-06-20 01:00:00 PT1H CPT1 0.0 2024-06-20 01:00:00 PT1H CQT1 11000.0 2024-06-20 01:00:00 PT1H CRC1 3750.0 2024-06-20 01:00:00 PT1H CSC1 1500.0 2024-06-20 01:00:00 PT1H CTG1 0.0

In [0]:
# Descargar archivo de Google Drive
download_url = f'https://drive.google.com/uc?export=download&id={id_archivo_balance_drive}'
local_file_path = '/tmp/balances3.xlsx'
response = requests.get(download_url)
with open(local_file_path, 'wb') as file:
    file.write(response.content)


In [0]:
#Base de datos de capacidad
df_archivo_capacidad = pd.read_excel(local_file_path, engine='openpyxl')
display(df_archivo_capacidad)

/databricks/spark/python/pyspark/sql/pandas/conversion.py:477: UserWarning: createDataFrame attempted Arrow optimization because 'spark.sql.execution.arrow.pyspark.enabled' is set to true; however, failed by the reason below:
  Expected bytes, got a 'datetime.datetime' object
Attempting non-optimization as 'spark.sql.execution.arrow.pyspark.fallback.enabled' is set to true.
  warn(msg)


Unnamed: 0 Unnamed: 1 Unnamed: 2 Unnamed: 3 Unnamed: 4 Unnamed: 5 NaN Programa de Generación por Planta NaN NaN NaN NaN NaN Empresa Generadora ACME S.A. E.S.P. NaN NaN NaN NaN NaN Despacho Real 10/07/2024 NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=0,HOUR_OF_DAY=0,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=1,HOUR_OF_DAY=1,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=2,HOUR_OF_DAY=2,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=3,HOUR_OF_DAY=3,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=4,HOUR_OF_DAY=4,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 20834 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=5,HOUR_OF_DAY=5,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 21626 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=6,HOUR_OF_DAY=6,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 26030 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_

# (T) Transformaciones




## Filtrado de Columnas

Nuestras fuentes, vienen en un estado crudo, o "raw", y hay datos, que no nos servirán para nuestro propósito, por lo cual, la primera transformación será quitar, o filtrar, los atributos que no se necesitan.

### (*T*) Filtrado de los atributos que traen el precio de bolsa, el despacho de las plantas


La documentación del API nos muestra que trae muchas columnas de información, denominados metadatos, necesitamos puntualmente los datos válidos para nuestro análisis. 

```
CodigoDuracion:string
CodigoPlanta:string
FechaHora:string
Valor:long
```

En estas 3 celdas, transformamos el formato utilizando funciones como aplanar o explotar, colocando alias y realizando un filtro o un select.

In [0]:
# Filtrar datos Primer Tabla de Precios de la Bolsa
columnas_requeridas_precios = ['Fecha', 'Valor', 'CodigoVariable','CodigoDuracion','UnidadMedida','Version']
if all(col in df_precios.columns for col in columnas_requeridas_precios):
    # Filtra solo las columnas requeridas
    df_precios_bolsa = df_precios[columnas_requeridas_precios]
    
    # Convierte 'FechaHora' a datetime con el formato correcto
    df_precios_bolsa['Fecha'] = pd.to_datetime(df_precios_bolsa['Fecha'], errors='coerce')
    
    # Extrae año, mes y día de la fecha
    df_precios_bolsa['anio'] = df_precios_bolsa['Fecha'].dt.year
    df_precios_bolsa['mes'] = df_precios_bolsa['Fecha'].dt.month
    df_precios_bolsa['dia'] = df_precios_bolsa['Fecha'].dt.day

else:
    print("Algunas columnas requeridas no están en df_precios.")
    df_precios_bolsa = pd.DataFrame()

display(df_precios_bolsa)

Fecha Valor CodigoVariable CodigoDuracion UnidadMedida Version anio mes dia 2024-06-20T00:00:00Z 322.0811 PPBOGReal P1D COP/kWh TXF 2024 6 20 2024-06-20T00:00:00Z 316.4945 PPBO P1D COP/kWh TXF 2024 6 20 2024-06-20T00:00:00Z 308.2125 PPBOGReal P1D COP/kWh TX2 2024 6 20 2024-06-20T00:00:00Z 302.7103 PPBO P1D COP/kWh TX2 2024 6 20 2024-06-20T00:00:00Z 316.9398 PPBO P1D COP/kWh TX3 2024 6 20 2024-06-20T00:00:00Z 322.5297 PPBOGReal P1D COP/kWh TX3 2024 6 20 2024-06-20T00:00:00Z 316.4859 PPBO P1D COP/kWh TXR 2024 6 20 2024-06-20T00:00:00Z 322.0841 PPBOGReal P1D COP/kWh TXR 2024 6 20 2024-06-20T00:00:00Z 308.2145 PPBOGReal P1D COP/kWh TX1 2024 6 20 2024-06-19T00:00:00Z 304.5383 PPBOGReal P1D COP/kWh TX2 2024 6 19 2024-06-19T00:00:00Z 296.5202 PPBO P1D COP/kWh TX2 2024 6 19 2024-06-19T00:00:00Z 304.6868 PPBOGReal P1D COP/kWh TX1 2024 6 19 2024-06-19T00:00:00Z 310.2923 PPBO P1D COP/kWh TXF 2024 6 19 2024-06-19T00:00:00Z 318.4077 PPBOGReal P1D COP/kWh TXF 2024 6 19 2024-06-19T00:00:00Z 311.186 PPBO P1D COP/kWh TX3 2024 6 19 2024-06-19T00:00:00Z 319.3001 PPBOGReal P1D COP/kWh TX3 2024 6 19 2024-06-19T00:00:00Z 310.2853 PPBO P1D COP/kWh TXR 2024 6 19 2024-06-19T00:00:00Z 318.4008 PPBOGReal P1D COP/kWh TXR 2024 6 19 2024-06-18T00:00:00Z 246.8571 PPBOGReal P1D COP/kWh TX3 2024 6 18 2024-06-18T00:00:00Z 239.8 PPBO P1D COP/kWh TX3 2024 6 18 2024-06-18T00:00:00Z 243.9286 PPBOGReal P1D COP/kWh TXF 2024 6 18 2024-06-18T00:00:00Z 236.8524 PPBO P1D COP/kWh TXF 2024 6 18 2024-06-18T00:00:00Z 236.855 PPBO P1D COP/kWh TXR 2024 6 18 2024-06-18T00:00:00Z 243.9302 PPBOGReal P1D COP/kWh TXR 2024 6 18 2024-06-18T00:00:00Z 223.2199 PPBO P1D COP/kWh TX2 2024 6 18 2024-06-18T00:00:00Z 230.0602 PPBOGReal P1D COP/kWh TX2 2024 6 18 2024-06-18T00:00:00Z 236.8389 PPBOGReal P1D COP/kWh TX1 2024 6 18 2024-06-17T00:00:00Z 262.5281 PPBOGReal P1D COP/kWh TX3 2024 6 17 2024-06-17T00:00:00Z 261.1931 PPBO P1D COP/kWh TX3 2024 6 17 2024-06-17T00:00:00Z 248.4987 PPBOGReal P1D COP/kWh TX2 2024 6 17 2024-06-17T00:00:00Z 247.0964 PPBO P1D COP/kWh TX2 2024 6 17 2024-06-17T00:00:00Z 248.4904 PPBOGReal P1D COP/kWh TX1 2024 6 17 2024-06-17T00:00:00Z 261.0419 PPBO P1D COP/kWh TXF 2024 6 17 2024-06-17T00:00:00Z 262.3524 PPBOGReal P1D COP/kWh TXF 2024 6 17 2024-06-17T00:00:00Z 261.0373 PPBO P1D COP/kWh TXR 2024 6 17 2024-06-17T00:00:00Z 262.3544 PPBOGReal P1D COP/kWh TXR 2024 6 17 2024-06-16T00:00:00Z 278.2515 PPBOGReal P1D COP/kWh TXF 2024 6 16 2024-06-16T00:00:00Z 276.6197 PPBO P1D COP/kWh TXF 2024 6 16 2024-06-16T00:00:00Z 264.3685 PPBOGReal P1D COP/kWh TX1 2024 6 16 2024-06-16T00:00:00Z 264.3774 PPBOGReal P1D COP/kWh TX2 2024 6 16 2024-06-16T00:00:00Z 262.811 PPBO P1D COP/kWh TX2 2024 6 16 2024-06-16T00:00:00Z 278.2651 PPBOGReal P1D COP/kWh TX3 2024 6 16 2024-06-16T00:00:00Z 276.6307 PPBO P1D COP/kWh TX3 2024 6 16 2024-06-16T00:00:00Z 276.6194 PPBO P1D COP/kWh TXR 2024 6 16 2024-06-16T00:00:00Z 278.2526 PPBOGReal P1D COP/kWh TXR 2024 6 16 2024-06-15T00:00:00Z 294.9338 PPBOGReal P1D COP/kWh TXF 2024 6 15 2024-06-15T00:00:00Z 290.0569 PPBO P1D COP/kWh TXF 2024 6 15 2024-06-15T00:00:00Z 274.5118 PPBO P1D COP/kWh TX2 2024 6 15 2024-06-15T00:00:00Z 275.5262 PPBOGReal P1D COP/kWh TX1 2024 6 15 2024-06-15T00:00:00Z 279.8025 PPBOGReal P1D COP/kWh TX2 2024 6 15 2024-06-15T00:00:00Z 294.9832 PPBOGReal P1D COP/kWh TX3 2024 6 15 2024-06-15T00:00:00Z 290.11 PPBO P1D COP/kWh TX3 2024 6 15 2024-06-15T00:00:00Z 294.9351 PPBOGReal P1D COP/kWh TXR 2024 6 15 2024-06-15T00:00:00Z 290.0608 PPBO P1D COP/kWh TXR 2024 6 15 2024-06-14T00:00:00Z 372.0906 PPBOGReal P1D COP/kWh TXR 2024 6 14 2024-06-14T00:00:00Z 370.9428 PPBO P1D COP/kWh TXR 2024 6 14 2024-06-14T00:00:00Z 370.9896 PPBO P1D COP/kWh TX3 2024 6 14 2024-06-14T00:00:00Z 372.1355 PPBOGReal P1D COP/kWh TX3 2024 6 14 2024-06-14T00:00:00Z 370.9397 PPBO P1D COP/kWh TXF 2024 6 14 2024-06-14T00:00:00Z 372.0884 PPBOGReal P1D COP/kWh TXF 2024 6 14 2024-06-14T00:00:00Z 358.223 PPBOGReal P1D COP/kWh TX2 2024 6 14 2024-06-14T00:00:00Z 357.0756 PPBO P1D COP

In [0]:
# Transformar datos de despachos
if 'FechaHora' in df_despachos.columns and 'Valor' in df_despachos.columns and 'CodigoPlanta' in df_despachos.columns:
    df_despachos['anio'] = pd.to_datetime(df_despachos['FechaHora']).dt.year
    df_despachos['mes'] = pd.to_datetime(df_despachos['FechaHora']).dt.month
    df_despachos['dia'] = pd.to_datetime(df_despachos['FechaHora']).dt.day
    df_despachos['hora'] = pd.to_datetime(df_despachos['FechaHora']).dt.hour
    df_despachos_transformed = df_despachos[['anio', 'mes', 'dia', 'hora', 'Valor', 'CodigoPlanta']]
    df_despachos_transformed = df_despachos_transformed.rename(columns={'Valor': 'capacidad_despacho', 'CodigoPlanta': 'codigo'})
else:
    print("Algunas columnas requeridas no están en df_despachos.")
    df_despachos_transformed = pd.DataFrame()

display(df_despachos_transformed)

anio mes dia hora capacidad_despacho codigo 2024 6 20 1 0.0 3EFY 2024 6 20 1 0.0 3ENA 2024 6 20 1 0.0 3ENE 2024 6 20 1 0.0 3EP6 2024 6 20 1 0.0 3EV1 2024 6 20 1 0.0 3EV3 2024 6 20 1 0.0 3EXB 2024 6 20 1 8150.0 3EXH 2024 6 20 1 0.0 3F5L 2024 6 20 1 0.0 3F5N 2024 6 20 1 0.0 3FCD 2024 6 20 1 0.0 3FCF 2024 6 20 1 0.0 3GI6 2024 6 20 1 0.0 3GJQ 2024 6 20 1 500.0 3GJU 2024 6 20 1 0.0 3GPZ 2024 6 20 1 0.0 3GRD 2024 6 20 1 0.0 3GSF 2024 6 20 1 0.0 3GVI 2024 6 20 1 0.0 3GVK 2024 6 20 1 0.0 3GVM 2024 6 20 1 9800.0 3H2U 2024 6 20 1 0.0 3HBN 2024 6 20 1 0.0 3HBP 2024 6 20 1 19920.0 3HDE 2024 6 20 1 19920.0 3HDG 2024 6 20 1 0.0 3HE8 2024 6 20 1 0.0 3HF5 2024 6 20 1 0.0 3HF7 2024 6 20 1 0.0 3HF9 2024 6 20 1 0.0 3HG7 2024 6 20 1 0.0 3HG9 2024 6 20 1 0.0 3HLD 2024 6 20 1 0.0 3HS9 2024 6 20 1 0.0 3HWM 2024 6 20 1 0.0 3HYG 2024 6 20 1 1000.0 3IJF 2024 6 20 1 0.0 3INX 2024 6 20 1 0.0 3IQA 2024 6 20 1 0.0 3IRX 2024 6 20 1 700.0 3IRZ 2024 6 20 1 0.0 3IS2 2024 6 20 1 0.0 3IZ6 2024 6 20 1 0.0 3J1J 2024 6 20 1 0.0 3J2B 2024 6 20 1 0.0 3J2H 2024 6 20 1 0.0 3J4D 2024 6 20 1 0.0 2TYI 2024 6 20 1 1400.0 2U1G 2024 6 20 1 0.0 2U5P 2024 6 20 1 19300.0 2U8Y 2024 6 20 1 19300.0 2U91 2024 6 20 1 19300.0 2U93 2024 6 20 1 1000.0 2UP2 2024 6 20 1 9000.0 2UPD 2024 6 20 1 9000.0 2UPF 2024 6 20 1 9000.0 2UPH 2024 6 20 1 9000.0 2UPJ 2024 6 20 1 750.0 2UR5 2024 6 20 1 16400.0 2UX3 2024 6 20 1 900.0 2V25 2024 6 20 1 400.0 2V27 2024 6 20 1 2900.0 2V5G 2024 6 20 1 0.0 2VJS 2024 6 20 1 7000.0 2WC5 2024 6 20 1 3000.0 2WFN 2024 6 20 1 0.0 2XXR 2024 6 20 1 1000.0 2YB9 2024 6 20 1 210.0 2YIR 2024 6 20 1 3100.0 2YNA 2024 6 20 1 3500.0 2YWY 2024 6 20 1 10000.0 2ZCF 2024 6 20 1 0.0 2ZHY 2024 6 20 1 0.0 2ZP9 2024 6 20 1 0.0 3A44 2024 6 20 1 0.0 3ACC 2024 6 20 1 380.0 3ADA 2024 6 20 1 1000.0 3AFQ 2024 6 20 1 200.0 3AQP 2024 6 20 1 0.0 3B4L 2024 6 20 1 0.0 3BZB 2024 6 20 1 200.0 3C3X 2024 6 20 1 0.0 3C3Z 2024 6 20 1 2800.0 3C4V 2024 6 20 1 4000.0 3CG9 2024 6 20 1 0.0 3CSH 2024 6 20 1 0.0 3DDT 2024 6 20 1 0.0 3DSO 2024 6 20 1 450.0 3DXJ 2024 6 20 1 0.0 3E7C 2024 6 20 1 8000.0 3E9I 2024 6 20 1 0.0 3EBN 2024 6 20 1 0.0 3ED1 2024 6 20 1 0.0 3EDL 2024 6 20 1 11480.0 3EE4 2024 6 20 1 2800.0 CCN1 2024 6 20 1 17000.0 CGM1 2024 6 20 1 498000.0 CHBG 2024 6 20 1 0.0 CHVR 2024 6 20 1 12500.0 CIP1 2024 6 20 1 0.0 CIS1 2024 6 20 1 10000.0 CLDR 2024 6 20 1 78000.0 CLL1 2024 6 20 1 0.0 CLMG 2024 6 20 1 7800.0 CMN1 2024 6 20 1 0.0 CMP2 2024 6 20 1 1100.0 COE1 2024 6 20 1 0.0 CPT1 2024 6 20 1 11000.0 CQT1 2024 6 20 1 3750.0 CRC1 2024 6 20 1 1500.0 CSC1 2024 6 20 1 0.0 CTG1 2024 6 20 1 0.0 CTG2 2024 6 20 1 0.0 CTG3 2024 6 20 1 44000.0 CUC1 2024 6 20 1 300.0 CUR1 2024 6 20 1 82000.0 DVS1 2024 6 20 1 0.0 ECU1 2024 6 20 1 0.0 ECU2 2024 6 20 1 0.0 EPFV 2024 6 20 1 28000.0 ESMR 2024 6 20 1 0.0 FLRD 2024 6 20 1 0.0 GCA1 2024 6 20 1 860.0 GCC1 2024 6 20 1 0.0 GE32 2024 6 20 1 110000.0 GEC3 2024 6 20 1 9500.0 GQA1 2024 6 20 1 0.0 GTPE 2024 6 20 1 434000.0 GTRG 2024 6 20 1 950350.0 GVIO 2024 6 20 1 0.0 GYPO 2024 6 20 1 55000.0 HMIN 2024 6 20 1 32000.0 HMLG 2024 6 20 1 18000.0 HMO1 2024 6 20 1 15000.0 HRD1 2024 6 20 1 22000.0 INC1 2024 6 20 1 16000.0 INS1 2024 6 20 1 0.0 INT1 2024 6 20 1 0.0 INZ1 2024 6 20 1 0.0 IQU1 2024 6 20 1 0.0 IQU2 2024 6 20 1 15000.0 IRG1 2024 6 20 1 0.0 3J4R 2024 6 20 1 0.0 3J4T 2024 6 20 1 0.0 3J4V 2024 6 20 1 0.0 3J83 2024 6 20 1 0.0 3J85 2024 6 20 1 0.0 3JBP 2024 6 20 1 4900.0 3JNR 2024 6 20 1 0.0 3JP6 2024 6 20 1 0.0 3JP8 2024 6 20 1 0.0 3JPA 2024 6 20 1 0.0 3JPC 2024 6 20 1 0.0 3JPE 2024 6 20 1 0.0 3JPK 2024 6 20 1 0.0 3JPM 2024 6 20 1 0.0 3JQA 2024 6 20 1 0.0 3JQC 2024 6 20 1 0.0 3JQE 2024 6 20 1 0.0 3K6T 2024 6 20 1 0.0 3K6X 2024 6 20 1 0.0 3K8A 2024 6 20 1 0.0 3K8C 2024 6 20 1 0.0 3K8E 2024 6 20 1 0.0 3KJK 2024 6 20 1 1000.0 3KL4 2024 6 20 1 4000.0 3KLQ 2024 6 20 1 0.0 3KOD 2024 6 20 1 0.0 3KOL 2024 6 20 1 0.0 3KVZ 2024 6 20 1 0.0 3KXQ 2024 6 20 1 0.0 3L9B 2024 6 20 1 3000.0 ABJ1 2024 6 20 1 7290.0 AFR1 2024 6 20 1 11000.0 ALBG 2024 6 20 1 6000.0 ALTG 2024 6 20 1 11000.0 AMA1 20

### (*T*) Filtrado de Plantas

El despacho trae todas las plantas, de nuevo, tenemos que filtrar, pero ahora solo debemos traer las que nos interesan, por ejemplo Zipaquirá, Guavio, Quimbo y Chivor, de la Empresa de Energía ACME. Lo haremos con SQL.

In [0]:
# Códigos específicos para filtrar de la tabla anterior por las generadoras que necesitamos
codigos_especificos = ['ZPA2', 'ZPA3', 'ZPA4', 'ZPA5', 'GVIO', 'QUI1', 'CHVR']

# Filtrar el DataFrame por los códigos específicos
dfDespachosAcme = df_despachos_transformed[df_despachos_transformed['codigo'].isin(codigos_especificos)]

# Mostrar el DataFrame filtrado
print("DataFrame filtrado por códigos específicos:")
display(dfDespachosAcme)

DataFrame filtrado por códigos específicos:


anio mes dia hora capacidad_despacho codigo 2024 6 20 1 0.0 CHVR 2024 6 20 1 950350.0 GVIO 2024 6 20 0 73000.0 QUI1 2024 6 20 0 0.0 CHVR 2024 6 20 0 972000.0 GVIO 2024 6 20 0 17000.0 ZPA2 2024 6 20 0 31000.0 ZPA3 2024 6 20 0 31000.0 ZPA4 2024 6 20 0 31000.0 ZPA5 2024 6 20 2 17000.0 ZPA2 2024 6 20 2 31000.0 ZPA3 2024 6 20 2 31000.0 ZPA4 2024 6 20 2 31000.0 ZPA5 2024 6 20 1 73000.0 QUI1 2024 6 20 1 17000.0 ZPA2 2024 6 20 1 31000.0 ZPA3 2024 6 20 1 31000.0 ZPA4 2024 6 20 1 31000.0 ZPA5 2024 6 20 16 120030.0 QUI1 2024 6 20 14 1215000.0 GVIO 2024 6 20 13 73000.0 QUI1 2024 6 20 14 0.0 CHVR 2024 6 20 17 73000.0 QUI1 2024 6 20 17 1215000.0 GVIO 2024 6 20 19 0.0 CHVR 2024 6 20 19 1215000.0 GVIO 2024 6 20 4 0.0 CHVR 2024 6 20 4 972000.0 GVIO 2024 6 20 3 73000.0 QUI1 2024 6 20 3 972000.0 GVIO 2024 6 20 12 0.0 CHVR 2024 6 20 13 0.0 CHVR 2024 6 20 12 31000.0 ZPA5 2024 6 20 12 31000.0 ZPA4 2024 6 20 12 31000.0 ZPA3 2024 6 20 12 17000.0 ZPA2 2024 6 20 4 73000.0 QUI1 2024 6 20 7 0.0 CHVR 2024 6 20 7 972000.0 GVIO 2024 6 20 6 17000.0 ZPA2 2024 6 20 6 31000.0 ZPA3 2024 6 20 6 31000.0 ZPA4 2024 6 20 6 31000.0 ZPA5 2024 6 20 7 73000.0 QUI1 2024 6 20 5 972000.0 GVIO 2024 6 20 4 31000.0 ZPA4 2024 6 20 4 31000.0 ZPA5 2024 6 20 10 0.0 CHVR 2024 6 20 10 972000.0 GVIO 2024 6 20 11 972000.0 GVIO 2024 6 20 11 0.0 CHVR 2024 6 20 8 73000.0 QUI1 2024 6 20 22 73000.0 QUI1 2024 6 20 20 17000.0 ZPA2 2024 6 20 20 31000.0 ZPA3 2024 6 20 20 31000.0 ZPA4 2024 6 20 20 33000.0 ZPA5 2024 6 20 21 1215000.0 GVIO 2024 6 20 3 17000.0 ZPA2 2024 6 20 3 31000.0 ZPA3 2024 6 20 3 31000.0 ZPA4 2024 6 20 3 31000.0 ZPA5 2024 6 20 4 17000.0 ZPA2 2024 6 20 4 31000.0 ZPA3 2024 6 20 2 0.0 CHVR 2024 6 20 2 73000.0 QUI1 2024 6 20 3 0.0 CHVR 2024 6 20 2 850040.0 GVIO 2024 6 20 23 31000.0 ZPA5 2024 6 20 23 31000.0 ZPA4 2024 6 20 23 31000.0 ZPA3 2024 6 20 23 17000.0 ZPA2 2024 6 20 23 73000.0 QUI1 2024 6 20 17 0.0 CHVR 2024 6 20 18 0.0 CHVR 2024 6 20 18 1215000.0 GVIO 2024 6 20 17 17000.0 ZPA2 2024 6 20 17 31000.0 ZPA3 2024 6 20 17 31000.0 ZPA4 2024 6 20 17 31000.0 ZPA5 2024 6 20 15 73000.0 QUI1 2024 6 20 16 17000.0 ZPA2 2024 6 20 16 31000.0 ZPA3 2024 6 20 16 31000.0 ZPA4 2024 6 20 16 31000.0 ZPA5 2024 6 20 20 0.0 CHVR 2024 6 20 20 1215000.0 GVIO 2024 6 20 20 316000.0 QUI1 2024 6 20 18 17000.0 ZPA2 2024 6 20 18 31000.0 ZPA3 2024 6 20 18 31000.0 ZPA4 2024 6 20 18 33000.0 ZPA5 2024 6 20 18 316000.0 QUI1 2024 6 20 19 316000.0 QUI1 2024 6 20 19 17000.0 ZPA2 2024 6 20 19 31000.0 ZPA3 2024 6 20 19 31000.0 ZPA4 2024 6 20 19 33000.0 ZPA5 2024 6 20 22 17000.0 ZPA2 2024 6 20 22 31000.0 ZPA3 2024 6 20 22 31000.0 ZPA4 2024 6 20 22 31000.0 ZPA5 2024 6 20 23 1215000.0 GVIO 2024 6 20 23 0.0 CHVR 2024 6 20 21 203510.0 QUI1 2024 6 20 14 73000.0 QUI1 2024 6 20 21 0.0 CHVR 2024 6 20 22 0.0 CHVR 2024 6 20 22 1215000.0 GVIO 2024 6 20 21 17000.0 ZPA2 2024 6 20 21 31000.0 ZPA3 2024 6 20 21 31000.0 ZPA4 2024 6 20 21 31000.0 ZPA5 2024 6 20 15 17000.0 ZPA2 2024 6 20 15 31000.0 ZPA3 2024 6 20 15 31000.0 ZPA4 2024 6 20 15 31000.0 ZPA5 2024 6 20 15 0.0 CHVR 2024 6 20 15 1215000.0 GVIO 2024 6 20 16 1215000.0 GVIO 2024 6 20 16 0.0 CHVR 2024 6 20 8 972000.0 GVIO 2024 6 20 8 0.0 CHVR 2024 6 20 7 31000.0 ZPA5 2024 6 20 7 31000.0 ZPA4 2024 6 20 7 31000.0 ZPA3 2024 6 20 7 17000.0 ZPA2 2024 6 20 9 972000.0 GVIO 2024 6 20 9 73000.0 QUI1 2024 6 20 8 31000.0 ZPA5 2024 6 20 8 31000.0 ZPA4 2024 6 20 8 31000.0 ZPA3 2024 6 20 8 17000.0 ZPA2 2024 6 20 9 0.0 CHVR 2024 6 20 5 31000.0 ZPA5 2024 6 20 5 31000.0 ZPA4 2024 6 20 5 31000.0 ZPA3 2024 6 20 5 17000.0 ZPA2 2024 6 20 6 0.0 CHVR 2024 6 20 5 0.0 CHVR 2024 6 20 5 73000.0 QUI1 2024 6 20 6 73000.0 QUI1 2024 6 20 6 972000.0 GVIO 2024 6 20 13 972000.0 GVIO 2024 6 20 13 31000.0 ZPA5 2024 6 20 13 31000.0 ZPA4 2024 6 20 13 31000.0 ZPA3 2024 6 20 13 17000.0 ZPA2 2024 6 20 14 31000.0 ZPA5 2024 6 20 14 31000.0 ZPA4 2024 6 20 14 31000.0 ZPA3 2024 6 20 14 17000.0 ZPA2 2024 6 20 10 31000.0 ZPA5 2024 6 20 10 31000.0 ZPA4 2024 6 20 10 31000.0 ZPA3 2024 6 20 10 17000.0 ZPA2 2024 6 20 9 31000.0 ZPA5

In [0]:
#Se hace la transformación del tipo de dato para aplicaar qué tipo de daato es y dar nombre a las columnas
from pyspark.sql.types import StructType, StructField, StringType, IntegerType

schemaArchivo = StructType([
    StructField("useless", StringType(), True),
    StructField("fecha", StringType(), True),
    StructField("planta", StringType(), True),
    StructField("generador", StringType(), True),
    StructField("capacidad", StringType(), True),
    StructField("codigo", StringType(), True)
])
df_archivo_capacidad_transformado = spark.createDataFrame(df_archivo_capacidad,schema=schemaArchivo)
df_archivo_capacidad_transformado.createOrReplaceTempView("CapacidadArchivo")
display(df_archivo_capacidad_transformado)


/databricks/spark/python/pyspark/sql/pandas/conversion.py:477: UserWarning: createDataFrame attempted Arrow optimization because 'spark.sql.execution.arrow.pyspark.enabled' is set to true; however, failed by the reason below:
  Exception thrown when converting pandas.Series (object) with name 'Unnamed: 1' to Arrow Array (string).
Direct cause: Expected bytes, got a 'datetime.datetime' object
Attempting non-optimization as 'spark.sql.execution.arrow.pyspark.fallback.enabled' is set to true.
  warn(msg)


useless fecha planta generador capacidad codigo NaN Programa de Generación por Planta NaN NaN NaN NaN NaN Empresa Generadora ACME S.A. E.S.P. NaN NaN NaN NaN NaN Despacho Real 10/07/2024 NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=0,HOUR_OF_DAY=0,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=1,HOUR_OF_DAY=1,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=2,HOUR_OF_DAY=2,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=3,HOUR_OF_DAY=3,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=4,HOUR_OF_DAY=4,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 20834 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=5,HOUR_OF_DAY=5,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 21626 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=6,HOUR_OF_DAY=6,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 26030 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_W

In [0]:
import numpy as np

# Verificación de la existencia de la columna 'generador'
if 'generador' in df_archivo_capacidad_transformado.columns:
    print("La columna 'generador' existe.")
else:
    raise ValueError("La columna 'generador' no existe en el DataFrame.")

# Verificación de los primeros registros del DataFrame
print("Primeros registros del DataFrame:")
print(df_archivo_capacidad)

# Verificación del tipo de datos de la columna 'generador'
print("Tipo de datos de la columna 'generador':")
print(df_archivo_capacidad_transformado['generador'].dtype)

# Intenta imprimir los valores únicos en la columna 'generador'
try:
    print("Valores únicos en la columna 'generador':")
    print(df_archivo_capacidad_transformado['generador'].unique())
except Exception as e:
    print(f"Error al obtener valores únicos: {e}")
display(df_archivo_capacidad_transformado)

La columna 'generador' existe.
Primeros registros del DataFrame:
     Unnamed: 0  ... Unnamed: 5
0           NaN  ...        NaN
1           NaN  ...        NaN
2           NaN  ...        NaN
3           NaN  ...        NaN
4           NaN  ...     CODIGO
..          ...  ...        ...
144         NaN  ...       QUI1
145         NaN  ...       QUI1
146         NaN  ...       QUI1
147         NaN  ...       QUI1
148         NaN  ...       QUI1

[149 rows x 6 columns]
Tipo de datos de la columna 'generador':
Column<'generador[dtype]'>
Valores únicos en la columna 'generador':
Error al obtener valores únicos: 'Column' object is not callable


useless fecha planta generador capacidad codigo NaN Programa de Generación por Planta NaN NaN NaN NaN NaN Empresa Generadora ACME S.A. E.S.P. NaN NaN NaN NaN NaN Despacho Real 10/07/2024 NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN FECHA PLANTA GENERADOR CAPACIDAD (Kwh) CODIGO NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=0,HOUR_OF_DAY=0,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=1,HOUR_OF_DAY=1,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=2,HOUR_OF_DAY=2,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=3,HOUR_OF_DAY=3,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 33000 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=4,HOUR_OF_DAY=4,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 20834 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=5,HOUR_OF_DAY=5,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 21626 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_WEEK=?,DAY_OF_WEEK_IN_MONTH=?,AM_PM=0,HOUR=6,HOUR_OF_DAY=6,MINUTE=0,SECOND=0,MILLISECOND=0,ZONE_OFFSET=?,DST_OFFSET=?] TERMOZIPA 2 26030 ZPA2 NaN java.util.GregorianCalendar[time=?,areFieldsSet=false,areAllFieldsSet=false,lenient=true,zone=sun.util.calendar.ZoneInfo[id="Etc/UTC",offset=0,dstSavings=0,useDaylight=false,transitions=0,lastRule=null],firstDayOfWeek=1,minimalDaysInFirstWeek=1,ERA=?,YEAR=2024,MONTH=6,WEEK_OF_YEAR=?,WEEK_OF_MONTH=?,DAY_OF_MONTH=10,DAY_OF_YEAR=?,DAY_OF_W

In [0]:
# Verificación de las columnas en df_archivo_capacidad
if all(col in df_archivo_capacidad.columns for col in ['anio', 'mes', 'dia', 'hora', 'codigo', 'capacidad_despacho']):
    # Verificación de las columnas en dfDespachosAcme
    if all(col in dfDespachosAcme.columns for col in ['anio', 'mes', 'dia', 'hora', 'codigo', 'capacidad_despacho']):
        # Unión de los DataFrames
        df_balance = pd.merge(
            df_archivo_capacidad,
            dfDespachosAcme,
            on=['anio', 'mes', 'dia', 'hora', 'codigo'],
            suffixes=('_capacidad', '_despacho')
        )
        
        # Calculo del balance
        df_balance['balance_disponible_horario'] = df_balance['capacidad'] - df_balance['capacidad_despacho']
        
        print("Balance calculado correctamente.")
    else:
        print("Algunas columnas requeridas no están en dfDespachosAcme.")
        df_balance = pd.DataFrame()
else:
    print("Algunas columnas requeridas no están en df_archivo_capacidad.")
    df_balance = pd.DataFrame()

print(df_balance)

Algunas columnas requeridas no están en df_archivo_capacidad.
Empty DataFrame
Columns: []
Index: []


In [0]:
# Calculo del consolidado
if 'balance_disponible_horario' in df_balance.columns:
    df_consolidado = df_balance.groupby(['anio', 'mes', 'dia', 'codigo']) \
                              .agg({'balance_disponible_horario': 'sum'}) \
                              .reset_index()
    print("Consolidado calculado correctamente.")
else:
    print("La columna 'balance_disponible_horario' no está en df_balance.")
    df_consolidado = pd.DataFrame()


La columna 'balance_disponible_horario' no está en df_balance.


In [0]:
# Calculo del compromiso
if 'Valor' in df_precios_filtrado.columns and 'codigo' in df_consolidado.columns and 'balance_disponible_horario' in df_consolidado.columns:
    df_consolidado = pd.merge(df_consolidado, df_precios_filtrado[['anio', 'mes', 'dia', 'Valor', 'codigo']],
                              on=['anio', 'mes', 'dia', 'codigo'], how='left')
    df_consolidado['Compromisos_MCOP'] = (df_consolidado['balance_disponible_horario'] * df_consolidado['Valor']) / 1000
    df_consolidado = df_consolidado[['anio', 'mes', 'dia', 'codigo', 'balance_disponible_horario', 'Compromisos_MCOP']]
    print("Compromisos calculados correctamente.")
else:
    print("Algunas columnas requeridas no están en los DataFrames.")
    df_consolidado = pd.DataFrame()

print(df_consolidado)


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-2555198705198800>, line 2
      1 # Calculo del compromiso
----> 2 if 'Valor' in df_precios_filtrado.columns and 'codigo' in df_consolidado.columns and 'balance_disponible_horario' in df_consolidado.columns:
      3     df_consolidado = pd.merge(df_consolidado, df_precios_filtrado[['anio', 'mes', 'dia', 'Valor', 'codigo']],
      4                               on=['anio', 'mes', 'dia', 'codigo'], how='left')
      5     df_consolidado['Compromisos_MCOP'] = (df_consolidado['balance_disponible_horario'] * df_consolidado['Valor']) / 1000

NameError: name 'df_precios_filtrado' is not defined

In [0]:
# Determinación de la operación
if 'Compromisos_MCOP' in df_consolidado.columns:
    df_consolidado['Operacion'] = df_consolidado['Compromisos_MCOP'].apply(lambda x: 'Comprar' if x < 0 else 'Vender')
    print("Operaciones determinadas correctamente.")
else:
    print("La columna 'Compromisos_MCOP' no está en df_consolidado.")
    df_consolidado['Operacion'] = pd.Series()

print(df_consolidado)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-2555198705198800>, line 2
      1 # Calculo del compromiso
----> 2 if 'Valor' in df_precios_filtrado.columns and 'codigo' in df_consolidado.columns and 'balance_disponible_horario' in df_consolidado.columns:
      3     df_consolidado = pd.merge(df_consolidado, df_precios_filtrado[['anio', 'mes', 'dia', 'Valor', 'codigo']],
      4                               on=['anio', 'mes', 'dia', 'codigo'], how='left')
      5     df_consolidado['Compromisos_MCOP'] = (df_consolidado['balance_disponible_horario'] * df_consolidado['Valor']) / 1000

NameError: name 'df_precios_filtrado' is not defined

##(*L*) Transferencia de Archivo de Resultados a Destino

Ahora tomamos el resultado de las compras y ventas de energía, lo consolidamos y guardamos en formato .CSV y después lo transferimos al destino para que lo cargue el usuario final.

Hice la simulación de la carga del archivo a un servicio de transferencia de archivos llamado https://fastupload.io

Para poder **cargar archivos**, hay que **iniciar sesión** en la plataforma, para ello se utiliza un API, https://fastupload.io/api#authorize , en el api, la plataforma iniciará sesión y obtendrá un token (secuencia de texto y números) que nos permitirá subir el archivo.

Para ello usamos otra API https://fastupload.io/api#file-upload, la cual nos pide algunos parámetros, como el nombre del archivo, el token, la cuenta y el folder, al final, al imprimir la respuesta, veremos que el arhivo fue cargado "File Uploaded".

In [0]:
# Guardado del archivo en CSV
output_csv_path = "/tmp/dfReporteCompraVentaEnergiaAcme.csv"
df_consolidado.to_csv(output_csv_path, index=False)


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-2555198705198800>, line 2
      1 # Calculo del compromiso
----> 2 if 'Valor' in df_precios_filtrado.columns and 'codigo' in df_consolidado.columns and 'balance_disponible_horario' in df_consolidado.columns:
      3     df_consolidado = pd.merge(df_consolidado, df_precios_filtrado[['anio', 'mes', 'dia', 'Valor', 'codigo']],
      4                               on=['anio', 'mes', 'dia', 'codigo'], how='left')
      5     df_consolidado['Compromisos_MCOP'] = (df_consolidado['balance_disponible_horario'] * df_consolidado['Valor']) / 1000

NameError: name 'df_precios_filtrado' is not defined

In [0]:
# Carga del archivo a mi servicio externo
params = {'key1': api_key_1, 'key2': api_key_2}
response = requests.get("https://fastupload.io/api/v2/authorize", params=params)
json_response = response.json()

file_upload_access_token = json_response.get("data", {}).get("access_token", "")
file_upload_account_id = json_response.get("data", {}).get("account_id", "")
with open(output_csv_path, "rb") as archivo:
    files = {"upload_file": (archivo.name, archivo)}
    data = {
        "access_token": file_upload_access_token,
        "account_id": file_upload_account_id,
        "folder_id": upload_folder_id
    }
    response = requests.post("https://fastupload.io/api/v2/file/upload", files=files, data=data)
    print(response.text)


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-2555198705198800>, line 2
      1 # Calculo del compromiso
----> 2 if 'Valor' in df_precios_filtrado.columns and 'codigo' in df_consolidado.columns and 'balance_disponible_horario' in df_consolidado.columns:
      3     df_consolidado = pd.merge(df_consolidado, df_precios_filtrado[['anio', 'mes', 'dia', 'Valor', 'codigo']],
      4                               on=['anio', 'mes', 'dia', 'codigo'], how='left')
      5     df_consolidado['Compromisos_MCOP'] = (df_consolidado['balance_disponible_horario'] * df_consolidado['Valor']) / 1000

NameError: name 'df_precios_filtrado' is not defined